In [3]:
!pip install geopandas


[notice] A new release of pip is available: 23.3.1 -> 25.0.1
[notice] To update, run: C:\Users\Dell\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [4]:
import pandas as pd
import numpy as np
import geopandas as gpd

from shapely.geometry import Point
from shapely.ops import unary_union

import folium
from folium.plugins import HeatMap, MarkerCluster
from folium import FeatureGroup, LayerControl

from sklearn.neighbors import KDTree

Visualize original points

In [6]:
# Step 1: Visualize original pedestrian measurement points

# Load pedestrian CSV (adjust path as needed)
ped_df = pd.read_csv(
    "src/scraping_correct/Datasets/trafiktaelling_fodg.csv", parse_dates=["taelle_dato"]
)
# Extract coordinates
ped_df["longitude"] = (
    ped_df["wkb_geometry"].str.extract(r"POINT \(([^ ]+)")[0].astype(float)
)
ped_df["latitude"] = (
    ped_df["wkb_geometry"].str.extract(r"POINT \([^ ]+ ([^ ]+)\)")[0].astype(float)
)

# Create a Folium map centered on Copenhagen
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# Add measurement points as CircleMarkers
for _, row in ped_df.iterrows():
    folium.CircleMarker(
        location=(row["latitude"], row["longitude"]),
        radius=4,
        fill=True,
        fill_opacity=0.7,
        popup=f"AADT: {row['aadt_fod_7_19']}<br>HVDT: {row['hvdt_fod_7_19']}",
    ).add_to(m)

# Display the map
m

Create a grid of point withing the copenaghen municipaly ( excluded Fredericksbarg which is a commun)

In [8]:
# 1) Load original pedestrian points
ped = pd.read_csv("src/scraping_correct/Datasets/trafiktaelling_fodg.csv")
ped["longitude"] = ped["wkb_geometry"].str.extract(r"POINT \(([^ ]+)")[0].astype(float)
ped["latitude"] = (
    ped["wkb_geometry"].str.extract(r"POINT \([^ ]+ ([^ ]+)\)")[0].astype(float)
)
ped_coords = ped[["latitude", "longitude"]].drop_duplicates()

# 2) Fetch and prepare Copenhagen boundary from GitHub
munis_url = (
    "https://raw.githubusercontent.com/"
    "magnuslarsen/geoJSON-Danish-municipalities/"
    "master/municipalities/municipalities.geojson"
)
munis = gpd.read_file(munis_url).to_crs(epsg=3857)
cph = munis[munis["label_dk"] == "København"]
cph_union = cph.unary_union

# 3) Generate a 100m grid within that boundary (metric CRS)
spacing = 200
minx, miny, maxx, maxy = cph_union.bounds
xs = np.arange(minx, maxx + spacing, spacing)
ys = np.arange(miny, maxy + spacing, spacing)
grid_points = [Point(x, y) for x in xs for y in ys]
grid_gdf = gpd.GeoDataFrame(geometry=grid_points, crs="EPSG:3857")
grid_inside = grid_gdf[grid_gdf.within(cph_union)]

# 4) Convert grid points to lat/lon
grid_latlon = grid_inside.to_crs(epsg=4326)
grid_coords = pd.DataFrame(
    {"latitude": grid_latlon.geometry.y, "longitude": grid_latlon.geometry.x}
)

print(f"Number of grid points: {len(grid_coords)}")

# 5) Create the Folium map
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# 6) Add measurement points (blue)
mc1 = MarkerCluster(name="Measurements").add_to(m)
for _, row in ped_coords.iterrows():
    folium.CircleMarker(
        location=(row.latitude, row.longitude),
        radius=4,
        color="blue",
        fill=True,
        fill_opacity=0.7,
    ).add_to(mc1)

# 7) Add grid points (red)
mc2 = MarkerCluster(name="Grid Points").add_to(m)
for _, row in grid_coords.iterrows():
    folium.CircleMarker(
        location=(row.latitude, row.longitude),
        radius=2,
        color="red",
        fill=True,
        fill_opacity=0.5,
    ).add_to(mc2)

# 8) Add layer control
folium.LayerControl().add_to(m)

# 9) Display the map
m

C:\Users\Dell\AppData\Local\Temp\ipykernel_11004\2905117344.py:17: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  cph_union = cph.unary_union


Number of grid points: 7062


In [9]:
# --- 1) Load your original measurement points ---
ped = pd.read_csv(
    "src/scraping_correct/Datasets/trafiktaelling_fodg.csv", parse_dates=["taelle_dato"]
)
ped["longitude"] = ped["wkb_geometry"].str.extract(r"POINT \(([^ ]+)")[0].astype(float)
ped["latitude"] = (
    ped["wkb_geometry"].str.extract(r"POINT \([^ ]+ ([^ ]+)\)")[0].astype(float)
)
ped = ped.dropna(subset=["latitude", "longitude"])
ped["aadt"] = pd.to_numeric(ped["aadt_fod_7_19"], errors="coerce")
ped["hvdt"] = pd.to_numeric(ped["hvdt_fod_7_19"], errors="coerce")
ped = ped.dropna(subset=["aadt", "hvdt"])

# Project to a metric CRS so distances are in meters
ped_gdf = gpd.GeoDataFrame(
    ped[["aadt", "hvdt", "longitude", "latitude"]],
    geometry=gpd.points_from_xy(ped.longitude, ped.latitude),
    crs="EPSG:4326",
).to_crs(epsg=3857)

# --- 2) Load your grid of new points (the 300+ clipped coords) ---
coords = grid_coords
grid = gpd.GeoDataFrame(
    coords,
    geometry=gpd.points_from_xy(coords.longitude, coords.latitude),
    crs="EPSG:4326",
).to_crs(epsg=3857)

# --- 3) Set up the IDW interpolation ---
xs = ped_gdf.geometry.x.values
ys = ped_gdf.geometry.y.values
aadt_vals = ped_gdf["aadt"].values
hvdt_vals = ped_gdf["hvdt"].values


def idw(pt, xs, ys, vals, power=3):
    dist = np.hypot(xs - pt.x, ys - pt.y)
    weights = 1.0 / (dist**power + 1e-6)
    return (weights * vals).sum() / weights.sum()


# --- 4) Compute interpolated values on every grid point ---
grid["aadt_fod_7_19"] = grid.geometry.apply(lambda p: idw(p, xs, ys, aadt_vals))
grid["hvdt_fod_7_19"] = grid.geometry.apply(lambda p: idw(p, xs, ys, hvdt_vals))

# --- 5) Reproject back to lat/lon and save ---
out = grid.to_crs(epsg=4326)
out["latitude"] = out.geometry.y
out["longitude"] = out.geometry.x

out[["latitude", "longitude", "aadt_fod_7_19", "hvdt_fod_7_19"]].to_csv(
    "expanded_pedestrian_traffic_interpolated.csv", index=False
)

print("Saved interpolated grid to expanded_pedestrian_traffic_interpolated.csv")

Saved interpolated grid to expanded_pedestrian_traffic_interpolated.csv


In [ ]:
# # --- 1) Load your original measurement points ---
# ped = pd.read_csv('trafiktaelling_fodg.csv', parse_dates=['taelle_dato'])
# ped['longitude'] = ped['wkb_geometry'].str.extract(r'POINT \(([^ ]+)')[0].astype(float)
# ped['latitude']  = ped['wkb_geometry'].str.extract(r'POINT \([^ ]+ ([^ ]+)\)')[0].astype(float)
# ped = ped.dropna(subset=['latitude','longitude'])
# ped['aadt'] = pd.to_numeric(ped['aadt_fod_7_19'], errors='coerce')
# ped['hvdt'] = pd.to_numeric(ped['hvdt_fod_7_19'], errors='coerce')
# ped = ped.dropna(subset=['aadt','hvdt'])

# # Project to a metric CRS so distances are in meters
# ped_gdf = gpd.GeoDataFrame(
#     ped[['aadt','hvdt','longitude','latitude']],
#     geometry=gpd.points_from_xy(ped.longitude, ped.latitude),
#     crs='EPSG:4326'
# ).to_crs(epsg=3857)

# # --- 2) Load your grid of new points (the 300+ clipped coords) ---
# coords = grid_coords
# grid = gpd.GeoDataFrame(
#     coords,
#     geometry=gpd.points_from_xy(coords.longitude, coords.latitude),
#     crs='EPSG:4326'
# ).to_crs(epsg=3857)

# # --- 3) Prepare KDTree for exact-match detection ---
# # Arrays of known point coords (x, y) and values
# xs = ped_gdf.geometry.x.values
# ys = ped_gdf.geometry.y.values
# points = np.vstack([xs, ys]).T
# aadt_vals = ped_gdf['aadt'].values
# hvdt_vals = ped_gdf['hvdt'].values

# tree = KDTree(points)

# # --- 4) Define enhanced IDW that preserves exact measurements ---
# def idw_exact(pt, xs, ys, vals, tree, power=3, tol=1e-3):
#     # Check for exact or near-exact match
#     dist_nn, idx_nn = tree.query([[pt.x, pt.y]], k=1)
#     if dist_nn[0][0] < tol:
#         return vals[idx_nn[0][0]]
#     # Otherwise perform IDW
#     d = np.hypot(xs - pt.x, ys - pt.y)
#     w = 1.0 / (d**power + 1e-6)
#     return (w * vals).sum() / w.sum()

# # --- 5) Compute interpolated values on every grid point ---
# grid['aadt_fod_7_19'] = grid.geometry.apply(
#     lambda p: idw_exact(p, xs, ys, aadt_vals, tree, power=3)
# )
# grid['hvdt_fod_7_19'] = grid.geometry.apply(
#     lambda p: idw_exact(p, xs, ys, hvdt_vals, tree, power=3)
# )

# # --- 6) Reproject back to lat/lon and save ---
# out = grid.to_crs(epsg=4326)
# out['latitude']  = out.geometry.y
# out['longitude'] = out.geometry.x

# out[['latitude','longitude','aadt_fod_7_19','hvdt_fod_7_19']].to_csv(
#     'expanded_pedestrian_traffic_interpolated_exact.csv',
#     index=False
# )

In [ ]:
# import pandas as pd
# import geopandas as gpd
# import numpy as np
# from shapely.geometry import Point
# from sklearn.neighbors import KDTree

# # --- 1) Load & prep your original points ---
# ped = pd.read_csv('trafiktaelling_fodg.csv', parse_dates=['taelle_dato'])
# ped['longitude'] = ped['wkb_geometry'].str.extract(r'POINT \(([^ ]+)')[0].astype(float)
# ped['latitude']  = ped['wkb_geometry'].str.extract(r'POINT \([^ ]+ ([^ ]+)\)')[0].astype(float)
# ped = ped.dropna(subset=['latitude','longitude'])
# ped['aadt'] = pd.to_numeric(ped['aadt_fod_7_19'], errors='coerce')
# ped['hvdt'] = pd.to_numeric(ped['hvdt_fod_7_19'], errors='coerce')
# ped = ped.dropna(subset=['aadt','hvdt'])

# # Project to metric CRS (so distances are in meters)
# ped_gdf = gpd.GeoDataFrame(
#     ped[['aadt','hvdt','longitude','latitude']],
#     geometry=gpd.points_from_xy(ped.longitude, ped.latitude),
#     crs='EPSG:4326'
# ).to_crs(epsg=3857)

# # --- 2) Load your grid of new points and clip (as before) ---
# coords = pd.read_csv('expanded_coords_full_cph.csv')
# grid = gpd.GeoDataFrame(
#     coords,
#     geometry=gpd.points_from_xy(coords.longitude, coords.latitude),
#     crs='EPSG:4326'
# ).to_crs(epsg=3857)

# # --- 3) Build KDTree for “exact match” checking ---
# xs = ped_gdf.geometry.x.values
# ys = ped_gdf.geometry.y.values
# points = np.vstack([xs, ys]).T
# aadt_vals = ped_gdf['aadt'].values
# hvdt_vals = ped_gdf['hvdt'].values
# tree = KDTree(points)

# # --- 4) Enhanced IDW that returns the exact value if the grid point
# #           falls right on a measurement. ---
# def idw_exact(pt, xs, ys, vals, tree, power=1, tol=1e-3):
#     dist_nn, idx_nn = tree.query([[pt.x, pt.y]], k=1)
#     if dist_nn[0][0] < tol:
#         return vals[idx_nn[0][0]]
#     d = np.hypot(xs - pt.x, ys - pt.y)
#     w = 1.0 / (d**power + 1e-6)
#     return (w * vals).sum() / w.sum()

# # --- 5) Interpolate AADT/HVDT onto every grid cell ---
# grid['aadt_fod_7_19'] = grid.geometry.apply(
#     lambda p: idw_exact(p, xs, ys, aadt_vals, tree, power=3)
# )
# grid['hvdt_fod_7_19'] = grid.geometry.apply(
#     lambda p: idw_exact(p, xs, ys, hvdt_vals, tree, power=3)
# )

# # --- 6) Bring everything back to lat/lon ---
# out = grid.to_crs(epsg=4326)
# out['latitude']  = out.geometry.y
# out['longitude'] = out.geometry.x
# interp = out[['latitude','longitude','aadt_fod_7_19','hvdt_fod_7_19']].copy()

# # --- 7) Convert the original points into the same 4‐col format ---
# orig = ped_gdf.to_crs(epsg=4326)
# orig['latitude']       = orig.geometry.y
# orig['longitude']      = orig.geometry.x
# orig['aadt_fod_7_19']  = orig['aadt']
# orig['hvdt_fod_7_19']  = orig['hvdt']
# orig = orig[['latitude','longitude','aadt_fod_7_19','hvdt_fod_7_19']]

# # --- 8) Concatenate & de-duplicate (so originals stay true) ---
# combined = pd.concat([interp, orig], ignore_index=True)
# combined = combined.drop_duplicates(subset=['latitude','longitude'])

# # --- 9) Save the final file ---
# combined.to_csv('expanded_pedestrian_traffic_with_originals.csv', index=False)
# print(f"Saved {len(combined)} rows (incl. originals) to expanded_pedestrian_traffic_with_originals.csv")

In [ ]:
import pandas as pd
import folium
from folium.plugins import HeatMap

# Adjust the path below if your CSV is named differently or in another folder
csv_path = "expanded_pedestrian_traffic_interpolated.csv"

# 1) Load the interpolated grid values
df = pd.read_csv(csv_path)

# 2) Initialize a Folium map centered on Copenhagen
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# 3) Prepare HeatMap data: [lat, lon, weight]
heat_data = df[["latitude", "longitude", "aadt_fod_7_19"]].values.tolist()

# 4) Add the HeatMap layer, using AADT (7–19) as the weight
HeatMap(
    data=heat_data,
    radius=30,  # radius of each “point”
    blur=30,  # smoothness
    min_opacity=0.3,  # allows visibility of base layer
).add_to(m)

# 5) Display the map
m

Plot original points on top of the heatmap 

In [ ]:
# 1) Load the interpolated heat‐grid
df_int = pd.read_csv("expanded_pedestrian_traffic_interpolated.csv")

# 2) Load the original measurements
ped = pd.read_csv("trafiktaelling_fodg.csv", parse_dates=["taelle_dato"])
ped["longitude"] = ped["wkb_geometry"].str.extract(r"POINT \(([^ ]+)")[0].astype(float)
ped["latitude"] = (
    ped["wkb_geometry"].str.extract(r"POINT \([^ ]+ ([^ ]+)\)")[0].astype(float)
)
ped["aadt"] = pd.to_numeric(ped["aadt_fod_7_19"], errors="coerce")
ped = ped.dropna(subset=["latitude", "longitude", "aadt"])

# 3) Create the map
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# 4) Add the interpolated heatmap
fg_heat = FeatureGroup(name="Interpolated AADT Heatmap")
heat_data = df_int[["latitude", "longitude", "aadt_fod_7_19"]].values.tolist()
HeatMap(heat_data, radius=25, blur=15, min_opacity=0.3).add_to(fg_heat)
fg_heat.add_to(m)

# 5) Add original points as markers
fg_pts = FeatureGroup(name="Original Measurement Points")
for _, row in ped.iterrows():
    folium.CircleMarker(
        location=(row["latitude"], row["longitude"]),
        radius=5,
        color="black",
        fill=True,
        fill_color="white",
        fill_opacity=0.8,
        popup=f"AADT: {row['aadt']}",
    ).add_to(fg_pts)
fg_pts.add_to(m)

# 6) Layer control
LayerControl().add_to(m)

# 7) Display
m